In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import descartes
import geopandas as gpd
import numpy as np
from shapely.geometry import Point, Polygon
import folium
import branca

In [2]:
# community_map = gpd.read_file('SHP/NYC_SHP/Original_Shp/neighbourhoods.geojson')
# community_map = community_map.rename(columns={'neighbourhood':'community'})

# df = pd.read_csv('./Data/NYC_Crimes.csv')
# crs = {'init' : 'epsg:4326'}
# df = df.dropna(subset=['Latitude'])
# df= df[df['Latitude'] != 0]

# geometry = [Point(xy) for xy in zip(df["Longitude"], df["Latitude"])]
# geometry[:3]


# geo_df = gpd.GeoDataFrame(df, crs = crs, geometry = geometry)

In [3]:
# community_map['community'].unique()

In [4]:
# taken from https://towardsdatascience.com/tagging-a-location-to-a-shapefile-area-using-geopandas-5d74336128bf
# geo_df['community'] = ''
# for idx in range(community_map.shape[0]):
#     #For every lat/long, find if they reside within a community
#     pip = geo_df.within(community_map.loc[idx, 'geometry'])
#     if pip.sum() > 0:
#         geo_df.loc[pip, 'community']  = community_map.loc[idx, 'community']

In [5]:
# taking group by and then reverting back to data frame to use
# https://technology.amis.nl/data-analytics/convert-groupby-result-on-pandas-data-frame-into-a-data-frame-using-to_frame/
# crimebycommunity = geo_df.groupby(['community'])['community'].count().to_frame(name = 'count').reset_index()


# crimebycommunity['community'].replace('', np.nan, inplace=True)
# crimebycommunity = crimebycommunity.dropna(subset=['community'])


# map_and_stats = community_map.merge(crimebycommunity, on="community")

# map_and_stats_2 = map_and_stats[['community','geometry','count']]

In [6]:
# map_and_stats_2.to_file("SHP/NYC_SHP/Summarized_Shp/NYCCrime.shp")

In [7]:
map_and_stats_2 = gpd.read_file("SHP/NYC_SHP/Summarized_Shp/NYCCrime.shp")

In [8]:
# https://vverde.github.io/blob/interactivechoropleth.html

x_map = map_and_stats_2.centroid.x.mean()
y_map = map_and_stats_2.centroid.y.mean()



mymap = folium.Map(location=[y_map, x_map], zoom_start=12,tiles=None)
folium.TileLayer('CartoDB positron',name="Light Map",control=False).add_to(mymap)


myscale = (map_and_stats_2['count'].quantile((0,0.25,0.9,1))).tolist()

/var/folders/9n/1h5nn1bn3ns9xx1s5nvxy5n40000gn/T/ipykernel_61331/136192827.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  x_map = map_and_stats_2.centroid.x.mean()
/var/folders/9n/1h5nn1bn3ns9xx1s5nvxy5n40000gn/T/ipykernel_61331/136192827.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  y_map = map_and_stats_2.centroid.y.mean()


In [9]:
mymap.choropleth(
geo_data=map_and_stats_2,
name='Choropleth',
data=map_and_stats_2,
columns=['community','count'],
key_on="feature.properties.community",
fill_color='Reds', #https://matplotlib.org/3.5.1/tutorials/colors/colormaps.html          sequential color maps
threshold_scale=myscale,
fill_opacity=0.5,
line_opacity=0.2,
legend_name='Crime Count',
smooth_factor=0
)

/opt/anaconda3/envs/geo_env/lib/python3.10/site-packages/folium/folium.py:409: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [10]:
mymap

In [11]:
style_function = lambda x: {'fillColor': '#ffffff',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}

highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}

In [12]:
CrimeCount = folium.features.GeoJson(
    map_and_stats_2,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['community','count'],
        aliases=['Neighborhood: ','Count of Crimes '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")
    )
)
mymap.add_child(CrimeCount)
mymap.keep_in_front(CrimeCount)
folium.LayerControl().add_to(mymap)

In [13]:
#this map should have the interactivity now
mymap

In [14]:
df_airbnb = pd.read_csv('./Data/NYC_listings.csv')


airbnb_locations = df_airbnb[['latitude','longitude']]
airbnb_list = airbnb_locations.values.tolist()

/var/folders/9n/1h5nn1bn3ns9xx1s5nvxy5n40000gn/T/ipykernel_61331/2968261049.py:1: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  df_airbnb = pd.read_csv('./Data/NYC_listings.csv')


In [15]:
df_airbnb.head()

id                                               name  host_id  \
0  2595                              Skylit Midtown Castle     2845   
1  3831  Whole flr w/private bdrm, bath & kitchen(pls r...     4869   
2  5121                                    BlissArtsSpace!     7356   
3  5136           Spacious Brooklyn Duplex, Patio + Garden     7378   
4  5178                   Large Furnished Room Near B'way　     8967   

     host_name neighbourhood_group       neighbourhood  latitude  longitude  \
0     Jennifer           Manhattan             Midtown  40.75356  -73.98559   
1  LisaRoxanne            Brooklyn  Bedford-Stuyvesant  40.68494  -73.95765   
2        Garon            Brooklyn  Bedford-Stuyvesant  40.68535  -73.95512   
3      Rebecca            Brooklyn         Sunset Park  40.66265  -73.99454   
4     Shunichi           Manhattan             Midtown  40.76457  -73.98317   

         room_type  price  minimum_nights  number_of_reviews last_review  \
0  Entire home/apt    150              30                 48  2019-11-04   
1  Entire home/apt     75               1                409  2021-10-22   
2     Private room     60              30                 50  2016-06-05   
3  Entire home/apt    275               5                  2  2021-08-08   
4     Private room     68               2                507  2021-11-08   

   reviews_per_month  calculated_host_listings_count  availability_365  \
0               0.33                               3               338   
1               4.86                               1               194   
2               0.52                               2               365   
3               0.02                               1               123   
4               3.68                               1               192   

   number_of_reviews_ltm license  
0                      0     NaN  
1                     32     NaN  
2                      0     NaN  
3                      1     NaN  
4                     33     NaN

In [16]:
def popup_html(row_num, df_airbnb):
    i = row_num
    name=df_airbnb['name'].iloc[i]
    price=df_airbnb['price'].iloc[i]
    roomtype=df_airbnb['room_type'].iloc[i]


    left_col_color = "#19a7bd"
    right_col_color = "#f2f0d3"

    html = """<!DOCTYPE html>
<html>

<head>
<h4 style="margin-bottom:10"; width="200px">{}</h4>""".format(name) + """

</head>
    <table style="height: 20px; width: 200px; border:1px solid black">
<tbody>
<tr style = "border:1px solid black">
<td style = "border:1px solid black">Price Per Night:</td>
<td style = "border:1px solid black">&nbsp; {}</td>""" .format(price) + """
</tr>

<tr style = "border:1px solid black">
<td style = "border:1px solid black">Room Type:</td>
<td style = "border:1px solid black">&nbsp; {}</td>""" .format(roomtype) + """
</tr>

</tbody>
</table>
</html>
"""
    return html

In [17]:
# set price to 200 for testing
price = 200
df_airbnb_price_filtered = df_airbnb[df_airbnb.price==price]
rows = len(df_airbnb_price_filtered)
#https://georgetsilva.github.io/posts/mapping-points-with-folium/
#https://towardsdatascience.com/folium-map-how-to-create-a-table-style-pop-up-with-html-code-76903706b88a
for point in range(0,rows):
    i = point
    html = popup_html(i,df_airbnb_price_filtered)
    iframe = branca.element.IFrame(html=html,width=200,height=200)
    popup = folium.Popup(folium.Html(html, script=True), max_width=500)
    folium.Marker(airbnb_list[point], popup).add_to(mymap)

In [18]:
mymap

In [19]:
# if you want to save html locally
# mymap.save("index_Chicago.html") 